In [1]:
import pandas as pd
import numpy as np

In [2]:
#summary_order = pd.read_excel(r'C:\Users\hoang\Google Drive\INFORM_COMPETITION\DATA\OtherTable\SummaryOrder.xlsx', sheet_name="All")
summary_order = pd.read_excel(r'C:\Users\hoang\Google Drive\INFORM_COMPETITION\DATA\OtherTable\SummaryOrder.xlsx', sheet_name="sum_s_f_p")
summary_rmi = pd.read_excel(r'C:\Users\hoang\Google Drive\INFORM_COMPETITION\DATA\OtherTable\SummaryRMI.xlsx', sheet_name="Sheet1")

In [3]:
# Read file
cs_df = pd.read_csv(r'C:\Users\hoang\Google Drive\INFORM_COMPETITION\DATA\Table 3\Classifier Split.csv')

# Rename columns: Fix space after column name
cs_df.columns = ['Color','Size','Percentage']

# Define all the colors
cs_color = cs_df['Color']
# Define all size
cs_size = cs_df['Size']
# Store percentage split in list
cs_pct_split = cs_df['Percentage']

# Combine color and size (tuple)
cs_color_size_list = list(zip(cs_color,cs_size))
# Dictionary for classifer for each color and size percentage
cs_color_size_pct_dict = dict(zip(cs_color_size_list,cs_pct_split))

In [4]:
#summary_order_new = summary_order.groupby(['Color','Packaging'],as_index=False).sum()

# Create dictionary to store qty for each combination of Color, Size, Flavor, Package Type
col_size_flavor_pack_qty_dict = dict(zip(list(zip(summary_order['Color'],
                                                  summary_order['Size'],
                                                  summary_order['Flavor'],
                                                  summary_order['Packaging'])),
                                         summary_order["Qty (pack unit)"]))
# Create dictionary to store pounds for each combination of Color, Size, Flavor, Package Type
col_size_flavor_pack_lbs_dict = dict(zip(list(zip(summary_order['Color'],
                                                  summary_order['Size'],
                                                  summary_order['Flavor'],
                                                  summary_order['Packaging'])),
                                         summary_order['Pound']))

flavor = ['F1','F2','F3','F4','F5','F6','F7','F8','F9','F10','F11','F12']

site = ['Columbus', 'Detroit', 'Green Bay', 'Omaha', 'Springfield']

color = ['Color Agent9', 'Color Agent5', 'Color Agent12', 'Color Agent33',
       'Color Agent8', 'Color Agent35', 'Color Agent18', 'Color Agent14',
       'Color Agent16', 'Color Agent22', 'Color Agent29', 'Color Agent38',
       'Color Agent37', 'Color Agent34', 'Color Agent6', 'Color Agent31',
       'Color Agent28', 'Color Agent2', 'Color Agent21', 'Color Agent7',
       'Color Agent36', 'Color Agent15', 'Color Agent20', 'Color Agent26',
       'Color Agent25', 'Color Agent3', 'Color Agent17', 'Color Agent4',
       'Color Agent1', 'Color Agent23', 'Color Agent30', 'Color Agent11',
       'Color Agent39', 'Color Agent19', 'Color Agent27', 'Color Agent32',
       'Color Agent10', 'Color Agent24', 'Color Agent13', 'Color Agent40']

size = ['S1','S2','S3','S4','S5']

packing = ['Box','Bag']

manu_cost = {('Columbus', 'Box'):261.30,
 ('Columbus', 'Bag'):27.50,
 ('Detroit', 'Box'):249.4,
 ('Detroit', 'Bag'):26.30,
 ('Green Bay', 'Box'):242.30,
 ('Green Bay', 'Bag'):25.50,
 ('Omaha', 'Box'):238.50,
 ('Omaha', 'Bag'):25.00,
 ('Springfield', 'Box'):273.10,
 ('Springfield', 'Bag'):28.80}

trans_distance_matrix = {('Columbus', 'Detroit'):210,
 ('Columbus', 'Green Bay'):530,
 ('Columbus', 'Omaha'):780,
 ('Columbus', 'Springfield'):630,
 ('Detroit', 'Columbus'):210,
 ('Detroit', 'Green Bay'):510,
 ('Detroit', 'Omaha'):730,
 ('Detroit', 'Springfield'):750,
 ('Green Bay', 'Columbus'):530,
 ('Green Bay', 'Detroit'):510,
 ('Green Bay', 'Omaha'):570,
 ('Green Bay', 'Springfield'):720,
 ('Omaha', 'Columbus'):780,
 ('Omaha', 'Detroit'):730,
 ('Omaha', 'Green Bay'):570,
 ('Omaha', 'Springfield'):630,
 ('Springfield', 'Columbus'):630,
 ('Springfield', 'Detroit'):750,
 ('Springfield', 'Green Bay'):720,
 ('Springfield', 'Omaha'):630}

rmi_dict = dict(zip(list(zip(summary_rmi['Location'],summary_rmi['Color'])),summary_rmi['Qty in pounds']))

# Create a detail dictionary of RMI for each site, color and size
rmi_size_dict = {}

for i in list(rmi_dict.keys()):
    for j in size:
        rmi_size_dict[i+(j,)] = rmi_dict[i] * cs_color_size_pct_dict[(i[1],j)]
#order_dict = dict(zip(list(zip(summary_order_new['Color'],summary_order_new['Package Type'])),summary_order_new['Qty']))

truck_load = 500000

cost_per_mile_50k_lbs = 3.5

box_weight = 2.5
bag_weight = 0.25

NOTE:
    
Only one color can be moved from one site to another.

In [5]:
list(rmi_dict.keys())[0]+('S1',)

('Columbus', 'Color Agent10', 'S1')

In [6]:
# Import package
from docplex.mp.model import Model

## Add Model

In [7]:
# create one model instance, with a name
m = Model(name='Inform')

## Add decision variables

In [8]:
# qty produce (number of unit) for each Color, Size, Flavor, Packaging 
qty_produce = { (s,c,si,f,p): m.integer_var(name= '{0} {1} {2} {3} {4}'.format(s,c,si,f,p))  
               for s in site 
               for c in color 
               for si in size
               for f in flavor 
               for p in packing }

## Add constaints

In [11]:
# Sum of output for each color and location (in pounds) <= input for that color and that site

# Box*2.5 lbs/box + Bag*0.25 lbs/bag
m.add_constraints( m.sum(qty_produce[s,c,si,f,'Box']*2.5 + qty_produce[s,c,si,f,'Bag']*0.25 
                         for si in size 
                         for f in flavor)  
                  <= 
                  rmi_size_dict.get((s,c,si),0) 
                  for s in site 
                  for c in color
                  for si in size) 

[docplex.mp.LinearConstraint[](2.500Columbus Color Agent9 S1 F1 Box+0.250Columbus Color Agent9 S1 F1 Bag+2.500Columbus Color Agent9 S1 F2 Box+0.250Columbus Color Agent9 S1 F2 Bag+2.500Columbus Color Agent9 S1 F3 Box+0.250Columbus Color Agent9 S1 F3 Bag+2.500Columbus Color Agent9 S1 F4 Box+0.250Columbus Color Agent9 S1 F4 Bag+2.500Columbus Color Agent9 S1 F5 Box+0.250Columbus Color Agent9 S1 F5 Bag+2.500Columbus Color Agent9 S1 F6 Box+0.250Columbus Color Agent9 S1 F6 Bag+2.500Columbus Color Agent9 S1 F7 Box+0.250Columbus Color Agent9 S1 F7 Bag+2.500Columbus Color Agent9 S1 F8 Box+0.250Columbus Color Agent9 S1 F8 Bag+2.500Columbus Color Agent9 S1 F9 Box+0.250Columbus Color Agent9 S1 F9 Bag+2.500Columbus Color Agent9 S1 F10 Box+0.250Columbus Color Agent9 S1 F10 Bag+2.500Columbus Color Agent9 S1 F11 Box+0.250Columbus Color Agent9 S1 F11 Bag+2.500Columbus Color Agent9 S1 F12 Box+0.250Columbus Color Agent9 S1 F12 Bag+2.500Columbus Color Agent9 S2 F1 Box+0.250Columbus Color Agent9 S2 F1 Bag+2

In [12]:
# Total Production must Meet demand
m.add_constraints( m.sum(qty_produce[(s,c,si,f,p)] for s in site)  
                  >= 
                  col_size_flavor_pack_qty_dict.get((c,si,f,p),0) 
                  for c in color 
                  for si in size
                  for f in flavor
                  for p in packing)

[docplex.mp.LinearConstraint[](Columbus Color Agent9 S1 F1 Box+Detroit Color Agent9 S1 F1 Box+Green Bay Color Agent9 S1 F1 Box+Omaha Color Agent9 S1 F1 Box+Springfield Color Agent9 S1 F1 Box,GE,0),
 docplex.mp.LinearConstraint[](Columbus Color Agent9 S1 F1 Bag+Detroit Color Agent9 S1 F1 Bag+Green Bay Color Agent9 S1 F1 Bag+Omaha Color Agent9 S1 F1 Bag+Springfield Color Agent9 S1 F1 Bag,GE,32544),
 docplex.mp.LinearConstraint[](Columbus Color Agent9 S1 F2 Box+Detroit Color Agent9 S1 F2 Box+Green Bay Color Agent9 S1 F2 Box+Omaha Color Agent9 S1 F2 Box+Springfield Color Agent9 S1 F2 Box,GE,0),
 docplex.mp.LinearConstraint[](Columbus Color Agent9 S1 F2 Bag+Detroit Color Agent9 S1 F2 Bag+Green Bay Color Agent9 S1 F2 Bag+Omaha Color Agent9 S1 F2 Bag+Springfield Color Agent9 S1 F2 Bag,GE,0),
 docplex.mp.LinearConstraint[](Columbus Color Agent9 S1 F3 Box+Detroit Color Agent9 S1 F3 Box+Green Bay Color Agent9 S1 F3 Box+Omaha Color Agent9 S1 F3 Box+Springfield Color Agent9 S1 F3 Box,GE,1500),
 do

In [13]:
# Minimize the Cost
manufacturing_cost = m.sum(qty_produce[(s,c,si,f,p)] * manu_cost[(s,p)]/100 
                           for s in site 
                           for c in color 
                           for si in size 
                           for f in flavor 
                           for p in packing ) 
m.minimize(manufacturing_cost)

Need something to model the factory capacity per day ( like how many pounds per day)

In [14]:
m.solve()

docplex.mp.solution.SolveSolution(obj=1.5339e+07,values={Detroit Color A..

---

In [10]:
from docplex.cp.model import *

In [11]:
model = CpoModel(name='informs')

In [12]:
# Read file
classifier_df = pd.read_csv(r'C:\Users\hoang\Google Drive\INFORM_COMPETITION\DATA\Table 9\Classifier.csv')

cl_site = classifier_df['Site']
cl_processing_rate = classifier_df['Processing_Rate']

cl_rate_dict = dict(zip(cl_site,cl_processing_rate))

# Pre-finish Rate (Reference)

In [13]:
# Read file
pre_finish_df = pd.read_csv(r'C:\Users\hoang\Google Drive\INFORM_COMPETITION\DATA\Table 10\Pre-finish.csv')
# Use average rate
pre_finish_df_new = pre_finish_df.groupby(['Site','Size','Flavor'],as_index= False).mean()

#
#pre_finish_detroit_df = pre_finish_df[pre_finish_df['Site'] =='Detroit']

pf_site = pre_finish_df_new['Site']
pf_size = pre_finish_df_new['Size']
pf_flavor = pre_finish_df_new['Flavor']
pf_processing_rate = pre_finish_df_new['Processing_Rate']

# Define list
pf_site_size_color_rate_list = list(zip(pf_site,pf_size,pf_flavor))

# Define dictionary to store processing rate
pf_site_size_color_rate_dict = dict(zip(pf_site_size_color_rate_list,pf_processing_rate))

# RMI Step (Raw Material Inventory Store)

In [14]:
# Read file
rmi_inventory_df = pd.read_csv(r'C:\Users\hoang\Google Drive\INFORM_COMPETITION\DATA\Table 2\RMI Inventory Level.csv')

# Create a dictionary store capacity & qty for each drum

# Create list
rmi_location = rmi_inventory_df['Location']
rmi_capacity = rmi_inventory_df['Capacity']
rmi_drum =  rmi_inventory_df['RMI Drum']
rmi_color = rmi_inventory_df['Color']
rmi_qty = rmi_inventory_df['Qty in pounds']

# Create list to store location & drum together
rmi_loc_drum_list = list(zip(rmi_location,rmi_drum))

# Create dictionary
rmi_loc_drum_color_dict = dict(zip(rmi_loc_drum_list,rmi_color))

rmi_loc_drum_cap_dict = dict(zip(rmi_loc_drum_list,rmi_capacity))

rmi_loc_drum_qty_dict = dict(zip(rmi_loc_drum_list,rmi_qty))

# Create new column to calculate the processing rate
condition = [rmi_inventory_df['Location'] == 'Detroit',
            rmi_inventory_df['Location'] == 'Columbus',
            rmi_inventory_df['Location'] == 'Green Bay',
            rmi_inventory_df['Location'] == 'Springfield',
            rmi_inventory_df['Location'] == 'Omaha']

choice = [3420,2280,2050,1260,4440]

rmi_inventory_df['Rate'] = np.select(condition,choice, default=0)
rmi_inventory_df['TimeProcess'] = rmi_inventory_df['Qty in pounds'] / rmi_inventory_df['Rate'] 

# fill na in rmi_inventory_df['TimeProcess']

rmi_inventory_df['TimeProcess'] = rmi_inventory_df['TimeProcess'].fillna(0)
# Create list
rmi_time_process= rmi_inventory_df['TimeProcess']
# Create dictionary to record time to process 

rmi_loc_drum_timeprocess_dict = dict(zip(rmi_loc_drum_list,rmi_time_process))

# Clasifier Step (Split into 5 sizes)

In [15]:
# Read file
cs_df = pd.read_csv(r'C:\Users\hoang\Google Drive\INFORM_COMPETITION\DATA\Table 3\Classifier Split.csv')

# Rename columns: Fix space after column name
cs_df.columns = ['Color','Size','Percentage']

# Define all the colors
cs_color = cs_df['Color']
# Define all size
cs_size = cs_df['Size']
# Store percentage split in list
cs_pct_split = cs_df['Percentage']

# Combine color and size (tuple)
cs_color_size_list = list(zip(cs_color,cs_size))
# Dictionary for classifer for each color and size percentage
cs_color_size_pct_dict = dict(zip(cs_color_size_list,cs_pct_split))

# PFI Step (Pre-finish Inventory: store in different drum: unique color & sizes)

In [16]:
# Read file
pfi_df = pd.read_csv(r'C:\Users\hoang\Google Drive\INFORM_COMPETITION\DATA\Table 7\Pre-finish Inventory Drum.csv')

# Filter only for detroits
#pfi_drum_detroit_df =  pfi_drum_df[pfi_drum_df['Site'] == 'Detroit, MI']

# Create list for location & capacity & drum
pfi_location = pfi_df['Location']
pfi_capacity = pfi_df['Capacity In pounds']
pfi_drum = pfi_df['Drum Number']

# Define list zip location and drum
pfi_loc_drum_list = list(zip(pfi_location,pfi_drum))

# Define dictionary
pfi_loc_drum_cap_dict = dict(zip(pfi_loc_drum_list,pfi_capacity))

# PFO Step (Pre-finish Operation: adding Flavors)

# FI Step ( Finishing Inventory: store in different drum: unique color & sizes & flavors)

In [17]:
# Read file
fi_df = pd.read_csv(r'C:\Users\hoang\Google Drive\INFORM_COMPETITION\DATA\Table 8\Pack inventory Drum.csv')

# Filter only for detroits
#pi_drum_detroit_df =  pi_drum_df[pi_drum_df['Site'] == 'Detroit, MI']

fi_location = fi_df['Location']
fi_capacity = fi_df['Capacity']
fi_drum = fi_df['Drum Number']

# Define list
fi_loc_drum = list(zip(fi_location,fi_drum))

# Define dictionary
fi_loc_drum_cap_dict = dict(zip(fi_loc_drum,fi_capacity))

In [18]:
# Interval variable

detroit_rmi_drum_list = ['RMI DRUM1','RMI DRUM2','RMI DRUM3','RMI DRUM4','RMI DRUM5','RMI DRUM6','RMI DRUM7',
'RMI DRUM8','RMI DRUM9','RMI DRUM10','RMI DRUM11','RMI DRUM12','RMI DRUM13','RMI DRUM14','RMI DRUM15','RMI DRUM16',
'RMI DRUM17','RMI DRUM18','RMI DRUM19','RMI DRUM20','RMI DRUM21','RMI DRUM22','RMI DRUM23','RMI DRUM24',
 'RMI DRUM25','RMI DRUM26','RMI DRUM27','RMI DRUM28','RMI DRUM29','RMI DRUM30','RMI DRUM31','RMI DRUM32',
 'RMI DRUM33','RMI DRUM34','RMI DRUM35','RMI DRUM36','RMI DRUM37','RMI DRUM38','RMI DRUM39','RMI DRUM40']

detroit_pfi_drum_list = ['PFI Drum1', 'PFI Drum2','PFI Drum3','PFI Drum4','PFI Drum5', 'PFI Drum6', 'PFI Drum7','PFI Drum8',
                         'PFI Drum9','PFI Drum10','PFI Drum11', 'PFI Drum12', 'PFI Drum13', 'PFI Drum14','PFI Drum15']

detroi_fi_drum_list = ['FI Drum 1','FI Drum 2','FI Drum 3','FI Drum 4','FI Drum 5','FI Drum 6','FI Drum 7','FI Drum 8']

In [25]:
merge_table = pd.read_csv(r'C:\Users\hoang\Google Drive\INFORM_COMPETITION\DATA\OtherTable\merge_table.csv')

In [43]:
# Calculate the total number of round pfi for each factory
loc_round_pfi_dict = merge_table.groupby('Location')['Round_PFI'].sum().to_dict()

merge_loc = merge_table['Location']
merge_rmi_drum = merge_table['RMI Drum']
merge_rmi_color = merge_table['Color']
merge_round_pfi = merge_table['Round_PFI']
merge_s1_qty = merge_table['S1_qty']
merge_s2_qty = merge_table['S2_qty']
merge_s3_qty = merge_table['S3_qty']
merge_s4_qty = merge_table['S4_qty']
merge_s5_qty = merge_table['S5_qty']
merge_s1_to_drum = merge_table['S1_TO_PFI_DRUM']
merge_s2_to_drum = merge_table['S2_TO_PFI_DRUM']
merge_s3_to_drum = merge_table['S3_TO_PFI_DRUM']
merge_s4_to_drum = merge_table['S4_TO_PFI_DRUM']
merge_s5_to_drum = merge_table['S5_TO_PFI_DRUM']

#
merge_loc_drum_round_pfi_dict = dict(zip(list(zip(merge_loc,merge_rmi_drum)),merge_round_pfi))
#
merge_loc_rmi_drum_s1_qty = dict(zip(list(zip(merge_loc,merge_rmi_drum)),merge_s1_qty))
merge_loc_rmi_drum_s2_qty = dict(zip(list(zip(merge_loc,merge_rmi_drum)),merge_s2_qty))
merge_loc_rmi_drum_s3_qty = dict(zip(list(zip(merge_loc,merge_rmi_drum)),merge_s3_qty))
merge_loc_rmi_drum_s4_qty = dict(zip(list(zip(merge_loc,merge_rmi_drum)),merge_s4_qty))
merge_loc_rmi_drum_s5_qty = dict(zip(list(zip(merge_loc,merge_rmi_drum)),merge_s5_qty))
merge_loc_rmi_drum_s1_to_pfi_drum = dict(zip(list(zip(merge_loc,merge_rmi_drum)),merge_s1_to_drum))
merge_loc_rmi_drum_s2_to_pfi_drum = dict(zip(list(zip(merge_loc,merge_rmi_drum)),merge_s2_to_drum))
merge_loc_rmi_drum_s3_to_pfi_drum = dict(zip(list(zip(merge_loc,merge_rmi_drum)),merge_s3_to_drum))
merge_loc_rmi_drum_s4_to_pfi_drum = dict(zip(list(zip(merge_loc,merge_rmi_drum)),merge_s4_to_drum))
merge_loc_rmi_drum_s5_to_pfi_drum = dict(zip(list(zip(merge_loc,merge_rmi_drum)),merge_s5_to_drum))

In [42]:
merge_table.head()

Location Name   RMI Drum          Color  Qty in pounds Capacity Location  \
0   Detroit, MI  RMI DRUM1  Color Agent21       300000.0  300,000  Detroit   
1   Detroit, MI  RMI DRUM2  Color Agent19       300000.0  300,000  Detroit   
2   Detroit, MI  RMI DRUM3  Color Agent16       300000.0  300,000  Detroit   
3   Detroit, MI  RMI DRUM4  Color Agent28       300000.0  300,000  Detroit   
4   Detroit, MI  RMI DRUM5  Color Agent25       300000.0  300,000  Detroit   

   S1  S2  S3  S4  ...  S5_cs_rate  S1_cs_pfi_drum_per_hr  \
0  26  20  20  18  ...       547.2                 0.0936   
1  31  18  19  18  ...       478.8                 0.1116   
2  25  12  17  26  ...       684.0                 0.0900   
3  20  17  25  14  ...       820.8                 0.0720   
4  18  25  26  13  ...       615.6                 0.0648   

   S2_cs_pfi_drum_per_hr  S3_cs_pfi_drum_per_hr  S4_cs_pfi_drum_per_hr  \
0                 0.0720                 0.0720                 0.0648   
1                 0.0648                 0.0684                 0.0648   
2                 0.0432                 0.0612                 0.0936   
3                 0.0612                 0.0900                 0.0504   
4                 0.0900                 0.0936                 0.0468   

   S5_cs_pfi_drum_per_hr  ProcessingTime  Total PFI Drum  NumberPFIDrum  \
0                 0.0576       87.719298              35             15   
1                 0.0504       87.719298              33             15   
2                 0.0720       87.719298              34             15   
3                 0.0864       87.719298              34             15   
4                 0.0648       87.719298              34             15   

   Round_PFI  
0          3  
1          3  
2          3  
3          3  
4          3  

[5 rows x 36 columns]

In [54]:
full_pfi_drum_list = [('Detroit',rmi,pfi,r) 
                      for rmi in detroit_rmi_drum_list
                      for pfi in detroit_pfi_drum_list
                      for r in range(1,merge_loc_drum_round_pfi_dict[('Detroit',rmi)]+1)] 

In [56]:
len(full_pfi_drum_list)

1635

In [40]:
full_pfi_drum_list = [(i,j) for i in range(loc_round_pfi_dict['Detroit']) for j in detroit_pfi_drum_list]


In [22]:
#
rmi_step = {('Detroit',rmi_drum): model.interval_var(size = int(rmi_loc_drum_timeprocess_dict[('Detroit',rmi_drum)])) 
            for rmi_drum in detroit_rmi_drum_list}
#
#max_no_drum = ('Detroit')
#
#pfi_step = {('Detroit',pfi_drum) model.interval_var(size = rmi_step ) for pfi_drum in pfi_loc_drum_list }

#rmi_step = {(s,rmi_drum): model.integer_var() for s in site for rmi_drum in detroit_rmi_drum_list}
#
#cs_step = {(s,): rmi_step[(s,rmi_drum)] }
#

SyntaxError: invalid syntax (<ipython-input-22-6d05efc80fa0>, line 7)

In [20]:
#merge
pfi_

Site Drum Number Capacity In pounds Location
0    Detroit, MI   PFI Drum1             10,000  Detroit
1    Detroit, MI   PFI Drum2             10,000  Detroit
2    Detroit, MI   PFI Drum3             10,000  Detroit
3    Detroit, MI   PFI Drum4             10,000  Detroit
4    Detroit, MI   PFI Drum5             10,000  Detroit
..           ...         ...                ...      ...
111    Omaha, NE  PFI Drum24              7,500    Omaha
112    Omaha, NE  PFI Drum25              7,500    Omaha
113    Omaha, NE  PFI Drum26              7,500    Omaha
114    Omaha, NE  PFI Drum27              7,500    Omaha
115    Omaha, NE  PFI Drum28              7,500    Omaha

[116 rows x 4 columns]

In [21]:
rmi_step

{('Detroit',
  'RMI DRUM1'): <docplex.cp.expression.CpoIntervalVar at 0x20005289148>,
 ('Detroit',
  'RMI DRUM2'): <docplex.cp.expression.CpoIntervalVar at 0x200052891c8>,
 ('Detroit',
  'RMI DRUM3'): <docplex.cp.expression.CpoIntervalVar at 0x20005289248>,
 ('Detroit',
  'RMI DRUM4'): <docplex.cp.expression.CpoIntervalVar at 0x200052892c8>,
 ('Detroit',
  'RMI DRUM5'): <docplex.cp.expression.CpoIntervalVar at 0x20005289348>,
 ('Detroit',
  'RMI DRUM6'): <docplex.cp.expression.CpoIntervalVar at 0x200052893c8>,
 ('Detroit',
  'RMI DRUM7'): <docplex.cp.expression.CpoIntervalVar at 0x20005289448>,
 ('Detroit',
  'RMI DRUM8'): <docplex.cp.expression.CpoIntervalVar at 0x200052894c8>,
 ('Detroit',
  'RMI DRUM9'): <docplex.cp.expression.CpoIntervalVar at 0x20005289548>,
 ('Detroit',
  'RMI DRUM10'): <docplex.cp.expression.CpoIntervalVar at 0x200052895c8>,
 ('Detroit',
  'RMI DRUM11'): <docplex.cp.expression.CpoIntervalVar at 0x20005289648>,
 ('Detroit',
  'RMI DRUM12'): <docplex.cp.expression